In [7]:
def Glassdoor_scraping(url):
    
    import requests
    import pandas as pd
    import numpy as np
    from bs4 import BeautifulSoup
    
    list_ = [] ; f_r = []
    #???what headers mean?
    headers = {'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_11_5) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/50.0.2661.102 Safari/537.36'}
    response = requests.get(url, headers=headers)
    results_page = BeautifulSoup(response.content,'html.parser')
    #title
    tag2 = results_page.find_all('h2', class_="h2 summary strong mt-0 mb-xsm")
    # work time
    tag3 = results_page.find_all('p', class_="mainText mb-0")
    #pros & cons
    tag4 = results_page.find_all('p', class_="mt-0 mb-xsm v2__EIReviewDetailsV2__bodyColor v2__EIReviewDetailsV2__lineHeightLarge")
    ####get sub_attributes ratings 
    tag5 = results_page.find_all('div',class_='subRatings module stars__StarsStyles__subRatings')

    sub_ratings=[]
    for item in tag5: 
        all_tag = list(map(lambda x:x.get_text(), item.find('ul',class_='undecorated')))
        sub_rating= list(map(lambda x:x.get('title'),item.find_all('span',class_='gdBars gdRatings med')))
        
        if 'Work/Life Balance' not in all_tag:
            sub_rating.insert(0,np.nan)
            
        if 'Culture & Values' not in all_tag:
            sub_rating.insert(1,np.nan)

        if 'Career Opportunities' not in all_tag:
            sub_rating.insert(2,np.nan)

        if 'Compensation and Benefits' not in all_tag:
            sub_rating.insert(3,np.nan)
            
        if 'Senior Management' not in all_tag:
            sub_rating.insert(4,np.nan)
 
        sub_ratings.append(sub_rating)

    ###get subrating
    sub_rate=[]; i = 0
    tag6 = results_page.find_all('span',class_='gdStars gdRatings sm stars__StarsStyles__gdStars')
    for item in tag6:
        if item.find('i',class_='subRatingsDrop'):
            sub_rate.append(sub_ratings[i])
            i = i+1
        else:
            sub_rate.append([np.nan,np.nan,np.nan,np.nan,np.nan])
  

    title = list(map(lambda x:x.get_text(),tag2))
    working_time = list(map(lambda x:x.get_text(),tag3))
    Pros = list(map(lambda x:x.get_text(),[i for i in tag4 if not tag4.index(i)%2]))
    Cons = list(map(lambda x:x.get_text(),[i for i in tag4 if tag4.index(i)%2]))
    if len(title) == len(sub_rate):
        list_.append(pd.DataFrame(list(zip(title,working_time,Pros,Cons)),columns =['Title','WorkTime','Pros','Cons']))
        s_r = pd.DataFrame(sub_rate,columns=['Work/Life Balance','Culture & Values','Career Opportunities','Compensation & Benefits','Senior Management'])
    

    while(True):
        next_page_link = results_page.find('li', class_="pagination__PaginationStyle__next").find('a').get('href')
        print(next_page_link)

####改动这里的页数！！如果想要爬几百页就break一次的话！！！！        
        if next_page_link == '/Reviews/IBM-Reviews-E354_P2001.htm':
            break
        
        response = requests.get('https://www.glassdoor.com'+next_page_link, headers=headers)
        results_page = BeautifulSoup(response.content,'html.parser')
        print(results_page)
        tag2 = results_page.find_all('h2', class_="h2 summary strong mt-0 mb-xsm")
        tag3 = results_page.find_all('p', class_="mainText mb-0")
        tag4 = results_page.find_all('p', class_="mt-0 mb-xsm v2__EIReviewDetailsV2__bodyColor v2__EIReviewDetailsV2__lineHeightLarge")
        
        ####get sub_attributes ratings 
        tag5 = results_page.find_all('div',class_='subRatings module stars__StarsStyles__subRatings')

        sub_ratings=[]
        for item in tag5: 
            # extract the text 'Work/Life Balance','Culture & Values','Career Opportunities' ,'Compensation and Benefits'&'Senior Management' from ul class_='undecorated'
            all_tag = list(map(lambda x:x.get_text(), item.find('ul',class_='undecorated')))
            sub_rating= list(map(lambda x:x.get('title'),item.find_all('span',class_='gdBars gdRatings med')))
            value = ['Work/Life Balance','Culture & Values','Career Opportunities' ,'Compensation and Benefits','Senior Management']
            if 'Work/Life Balance' not in all_tag:
                sub_rating.insert(0,np.nan)

            if 'Culture & Values' not in all_tag:
                sub_rating.insert(1,np.nan)

            if 'Career Opportunities' not in all_tag:
                sub_rating.insert(2,np.nan)

            if 'Compensation and Benefits' not in all_tag:
                sub_rating.insert(3,np.nan)

            if 'Senior Management' not in all_tag:
                sub_rating.insert(4,np.nan)

            sub_ratings.append(sub_rating)

        ###get subrating
        sub_rate=[]; i = 0
        tag6 = results_page.find_all('span',class_='gdStars gdRatings sm stars__StarsStyles__gdStars')
        for item in tag6:
            if item.find('i',class_='subRatingsDrop'):
                sub_rate.append(sub_ratings[i])
                i = i+1
            else:
                sub_rate.append([np.nan,np.nan,np.nan,np.nan,np.nan])
        
        
        title = list(map(lambda x:x.get_text(),tag2))
        working_time = list(map(lambda x:x.get_text(),tag3))
        Pros = list(map(lambda x:x.get_text(),[i for i in tag4 if not tag4.index(i)%2]))
        Cons = list(map(lambda x:x.get_text(),[i for i in tag4 if tag4.index(i)%2]))

       
        if title:
            if len(title) == len(sub_rate):
                list_.append(pd.DataFrame(list(zip(title,working_time,Pros,Cons)),columns =['Title','WorkTime','Pros','Cons']))
                s_r = pd.concat([s_r, pd.DataFrame(sub_rate,columns=['Work/Life Balance','Culture & Values','Career Opportunities','Compensation & Benefits','Senior Management'])])
        else:
            break
#         break
        
    
    result = pd.concat(list_)
    result = result.reset_index(drop = True)
    s_r = s_r.reset_index(drop=True)
#     print(s_r)
    final_result = pd.concat([result,s_r],axis=1)

    return final_result

In [8]:
IBM_1 = Glassdoor_scraping(url = 'https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1001.htm')

/Reviews/IBM-Reviews-E354_P1002.htm
<!DOCTYPE html>

<html class="flex" lang="en" xmlns:fb="http://www.facebook.com/2008/fbml" xmlns:og="http://opengraph.org/schema/">
<head prefix="og: http://ogp.me/ns# fb: http://ogp.me/ns/fb# glassdoor: http://ogp.me/ns/fb/glassdoor#">
<meta content="49,463 IBM reviews. A free inside look at company reviews and salaries posted anonymously by employees." name="description"/><meta content="49,463 IBM reviews. A free inside look at company reviews and salaries posted anonymously by employees." name="og:description"/>
<link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1002.htm" rel="canonical"/><link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1001.htm" rel="prev"/><link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1003.htm" rel="next"/>
<!-- because the getter clears the value --><script>
	window.gdGlobals = window.gdGlobals ||
		[{
			'analyticsId':                      "UA-2595786-1",

			
			'analyticsUrl':   

<!DOCTYPE html>

<html class="flex" lang="en" xmlns:fb="http://www.facebook.com/2008/fbml" xmlns:og="http://opengraph.org/schema/">
<head prefix="og: http://ogp.me/ns# fb: http://ogp.me/ns/fb# glassdoor: http://ogp.me/ns/fb/glassdoor#">
<meta content="49,463 IBM reviews. A free inside look at company reviews and salaries posted anonymously by employees." name="description"/><meta content="49,463 IBM reviews. A free inside look at company reviews and salaries posted anonymously by employees." name="og:description"/>
<link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1003.htm" rel="canonical"/><link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1002.htm" rel="prev"/><link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1004.htm" rel="next"/>
<!-- because the getter clears the value --><script>
	window.gdGlobals = window.gdGlobals ||
		[{
			'analyticsId':                      "UA-2595786-1",

			
			'analyticsUrl':                     "/employerInfo/Rev

<!DOCTYPE html>

<html class="flex" lang="en" xmlns:fb="http://www.facebook.com/2008/fbml" xmlns:og="http://opengraph.org/schema/">
<head prefix="og: http://ogp.me/ns# fb: http://ogp.me/ns/fb# glassdoor: http://ogp.me/ns/fb/glassdoor#">
<meta content="49,463 IBM reviews. A free inside look at company reviews and salaries posted anonymously by employees." name="description"/><meta content="49,463 IBM reviews. A free inside look at company reviews and salaries posted anonymously by employees." name="og:description"/>
<link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1004.htm" rel="canonical"/><link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1003.htm" rel="prev"/><link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1005.htm" rel="next"/>
<!-- because the getter clears the value --><script>
	window.gdGlobals = window.gdGlobals ||
		[{
			'analyticsId':                      "UA-2595786-1",

			
			'analyticsUrl':                     "/employerInfo/Rev

<!DOCTYPE html>

<html class="flex" lang="en" xmlns:fb="http://www.facebook.com/2008/fbml" xmlns:og="http://opengraph.org/schema/">
<head prefix="og: http://ogp.me/ns# fb: http://ogp.me/ns/fb# glassdoor: http://ogp.me/ns/fb/glassdoor#">
<meta content="49,463 IBM reviews. A free inside look at company reviews and salaries posted anonymously by employees." name="description"/><meta content="49,463 IBM reviews. A free inside look at company reviews and salaries posted anonymously by employees." name="og:description"/>
<link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1005.htm" rel="canonical"/><link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1004.htm" rel="prev"/><link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1006.htm" rel="next"/>
<!-- because the getter clears the value --><script>
	window.gdGlobals = window.gdGlobals ||
		[{
			'analyticsId':                      "UA-2595786-1",

			
			'analyticsUrl':                     "/employerInfo/Rev

<!DOCTYPE html>

<html class="flex" lang="en" xmlns:fb="http://www.facebook.com/2008/fbml" xmlns:og="http://opengraph.org/schema/">
<head prefix="og: http://ogp.me/ns# fb: http://ogp.me/ns/fb# glassdoor: http://ogp.me/ns/fb/glassdoor#">
<meta content="49,463 IBM reviews. A free inside look at company reviews and salaries posted anonymously by employees." name="description"/><meta content="49,463 IBM reviews. A free inside look at company reviews and salaries posted anonymously by employees." name="og:description"/>
<link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1006.htm" rel="canonical"/><link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1005.htm" rel="prev"/><link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1007.htm" rel="next"/>
<!-- because the getter clears the value --><script>
	window.gdGlobals = window.gdGlobals ||
		[{
			'analyticsId':                      "UA-2595786-1",

			
			'analyticsUrl':                     "/employerInfo/Rev

<!DOCTYPE html>

<html class="flex" lang="en" xmlns:fb="http://www.facebook.com/2008/fbml" xmlns:og="http://opengraph.org/schema/">
<head prefix="og: http://ogp.me/ns# fb: http://ogp.me/ns/fb# glassdoor: http://ogp.me/ns/fb/glassdoor#">
<meta content="49,463 IBM reviews. A free inside look at company reviews and salaries posted anonymously by employees." name="description"/><meta content="49,463 IBM reviews. A free inside look at company reviews and salaries posted anonymously by employees." name="og:description"/>
<link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1007.htm" rel="canonical"/><link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1006.htm" rel="prev"/><link href="https://www.glassdoor.com/Reviews/IBM-Reviews-E354_P1008.htm" rel="next"/>
<!-- because the getter clears the value --><script>
	window.gdGlobals = window.gdGlobals ||
		[{
			'analyticsId':                      "UA-2595786-1",

			
			'analyticsUrl':                     "/employerInfo/Rev

AttributeError: 'NoneType' object has no attribute 'find'

In [15]:
baidu

Title  \
0     "Good to join as fresher, IBM is best for lear...   
1                                      "Underestimated"   
2                           "Associate system engineer"   
3                                     "Data specialist"   
4                               "Application Developer"   
...                                                 ...   
6625                             "World Class Thinking"   
6626                                   "Good for start"   
6627                                              "IBM"   
6628                        "Associate System Engineer"   
6629                              "Best company so far"   

                                               WorkTime  \
0     I have been working at IBM full-time for more ...   
1     I have been working at IBM full-time for more ...   
2     I have been working at IBM full-time for more ...   
3                  I have been working at IBM full-time   
4                             I worked at IBM full-time   
...                                                 ...   
6625     I worked at IBM full-time for more than a year   
6626                          I worked at IBM full-time   
6627  I have been working at IBM full-time for less ...   
6628                          I worked at IBM full-time   
6629                          I worked at IBM full-time   

                                                   Pros  \
0     --&gt; Good learning opportunity, mandatory to...   
1                    To gain some experience for future   
2                I m working in IBM from last two years   
3                       Good company to learn and grow.   
4                     Good company to start your career   
...                                                 ...   
6625  You are surrounded by leading minds and leadin...   
6626  If you are starting in IT, IBM is one of the b...   
6627  Good work- life balance.\r\nWorking with cutti...   
6628  1) Multinational Company where you can directl...   
6629                   Good starting salary for fresher   

                                                   Cons Work/Life Balance  \
0     Very low pay (independent of performance due t...               5.0   
1                         Good team and interesting job               4.0   
2     Worst Management . they will not give good rat...               4.0   
3                                Growth is slow in ibm.               4.0   
4                   Learning opportunities was less and               5.0   
...                                                 ...               ...   
6625  Like most consultancies, the pace can be frene...               3.0   
6626  Your salary probably won't increase in first 2...               4.0   
6627  Big changes in the past few years which create...               4.0   
6628                             1) Not an average hike               5.0   
6629                       no cons\r\nno advice to mgmt               NaN   

     Culture & Values Career Opportunities Compensation & Benefits  \
0                 5.0                  5.0                     3.0   
1                 3.0                  4.0                     1.0   
2                 4.0                  3.0                     3.0   
3                 4.0                  4.0                     3.0   
4                 5.0                  4.0                     4.0   
...               ...                  ...                     ...   
6625              4.0                  5.0                     5.0   
6626              4.0                  4.0                     2.0   
6627              4.0                  2.0                     3.0   
6628              4.0                  3.0                     2.0   
6629              NaN                  NaN                     NaN   

     Senior Management  
0                  5.0  
1                  1.0  
2                  4.0  
3                  4.0  
4                  5.0  
...    

In [17]:
baidu1

Title  \
0                   "Good for start"   
1                              "IBM"   
2        "Associate System Engineer"   
3              "Best company so far"   
4     "BEST IT Complex Organization"   
...                              ...   
1785            "NICE PLACE TO WORK"   
1786                           "IBM"   
1787               "System engineer"   
1788                     "Architect"   
1789    "Great company to work with"   

                                               WorkTime  \
0                             I worked at IBM full-time   
1     I have been working at IBM full-time for less ...   
2                             I worked at IBM full-time   
3                             I worked at IBM full-time   
4     I have been working at IBM full-time for more ...   
...                                                 ...   
1785  I have been working at IBM full-time for less ...   
1786               I have been working at IBM full-time   
1787                          I worked at IBM full-time   
1788  I have been working at IBM full-time for less ...   
1789                                   I worked at IBM    

                                                   Pros  \
0     If you are starting in IT, IBM is one of the b...   
1     Good work- life balance.\r\nWorking with cutti...   
2     1) Multinational Company where you can directl...   
3                      Good starting salary for fresher   
4     Best IT service company to work with, long ter...   
...                                                 ...   
1785    REALISTIC WORK PLACE, GET SATISFACTION FROM JOB   
1786  Flexibility.Innovation,Trust and personal Resp...   
1787     Great for women to work\r\nfriendly colleagues   
1788  Flexible hrs,trusting employees,lot of opportu...   
1789  Great work life balance. Employee friendly pol...   

                                                   Cons Work/Life Balance  \
0     Your salary probably won't increase in first 2...               4.0   
1     Big changes in the past few years which create...               4.0   
2                                1) Not an average hike               5.0   
3                          no cons\r\nno advice to mgmt               NaN   
4     Salary Increment is conservative, Internal pro...               3.0   
...                                                 ...               ...   
1785  work in village so if can cope up in such envi...               3.0   
1786                 Offers Less Hike to the employees.               4.0   
1787  If enter at lowest level of hierarchy then the...               NaN   
1788             vision unclear sometimes,lost in ocean               4.0   
1789  Haven't seen many cons in the time I have work...               5.0   

     Culture & Values Career Opportunities Compensation & Benefits  \
0                 4.0                  4.0                     2.0   
1                 4.0                  2.0                     3.0   
2                 4.0                  3.0                     2.0   
3                 NaN                  NaN                     NaN   
4                 5.0                  5.0                     2.0   
...               ...                  ...                     ...   
1785              5.0                  3.0                     3.0   
1786              4.0                  4.0                     4.0   
1787              NaN                  NaN                     NaN   
1788              5.0                  4.0                     3.0   
1789              4.0                  4.0                     3.0   

     Senior Management  
0                  2.0  
1                  3.0  
2                  3.0  
3                  NaN  
4                  3.0  
...                ...  
1785               4.0  
1786               4.0  
1787               NaN  
1788               4.0  
1789               4.0  

[1790 rows x 9 columns]

In [21]:
baidu2

Title  \
0                "Great company to work with"   
1                     "Application Developer"   
2    "Business Support Operations Specialist"   
3                         "Software engineer"   
4                                      "Good"   
..                                        ...   
125                              "Technology"   
126                           "Summer Intern"   
127         "Once an IBMer an IBMer for life"   
128                     "Best in IT industry"   
129                                 "IBM ISL"   

                                              WorkTime  \
0                                     I worked at IBM    
1       I worked at IBM full-time for more than a year   
2                            I worked at IBM full-time   
3      I worked at IBM full-time for more than 3 years   
4      I worked at IBM full-time for more than 5 years   
..                                                 ...   
125                        I have been working at IBM    
126                                   I worked at IBM    
127  I have been working at IBM full-time for less ...   
128                          I worked at IBM full-time   
129  I have been working at IBM full-time for more ...   

                                                  Pros  \
0    Great work life balance. Employee friendly pol...   
1                    Flexibility in time; Job security   
2    Great manager, great team, nice office, paid o...   
3    Light workload . Flexible working hour. Nice c...   
4                   Work From Home option is available   
..                                                 ...   
125       Multiple projects to try any different tasks   
126               good environment and good colleagues   
127  The Brand of IBM\r\nLots of Learning and Growt...   
128  Good Atmosphere in the campus\r\nNice Infrastr...   
129    1. Work from home option\r\n2. Flexible timings   

                                                  Cons Work/Life Balance  \
0    Haven't seen many cons in the time I have work...               5.0   
1          Remuneration just like any other IT company               4.0   
2          Rather hectic environment, lots of overtime               NaN   
3    Limited bonus. Low salary. Limited opportuniti...               3.0   
4    Less salary\r\nNo hikes\r\nFavoritism\r\nProce...               2.0   
..                                                 ...               ...   
125                       I do not think there is cons               5.0   
126                              far away from my home               5.0   
127  An Ocean .Tough to get Recognized.\r\nAnnual I...               5.0   
128                 Any process ran slow in the campus               NaN   
129  1. Yearly hike are not that much good.\r\n2. y...               5.0   

    Culture & Values Career Opportunities Compensation & Benefits  \
0                4.0                  4.0                     3.0   
1                3.0                  4.0                     2.0   
2                NaN                  NaN                     NaN   
3                3.0                  3.0                     3.0   
4                2.0                  3.0                     1.0   
..               ...                  ...                     ...   
125              5.0                  5.0                     5.0   
126              4.0                  4.0                     4.0   
127              5.0                  4.0                     1.0   
128              NaN                  NaN                     NaN   
129              3.0                  3.0                     2.0   

    Senior Management  
0                 4.0  
1                 3.0  
2                 NaN  
3                 3.0  
4                 3.0  
..                ...  
125               5.0  
126               4.0  
127               3.0  
128               NaN  
129               4.0  

[130 rows x 9 columns]

In [22]:
baidu3

Title  \
0                                     "Project Manager"   
1                          "short review for IBM china"   
2                                                 "Ibm"   
3                                      "Good Prospects"   
4                      "excellent company to work with"   
...                                                 ...   
1445  "Flexible, can support learning but not good pay"   
1446                  "Explore knowledge and learnings"   
1447                                "SAP SD Consultant"   
1448                     "Management is too old-school"   
1449               "Great company to start your Career"   

                                               WorkTime  \
0     I have been working at IBM full-time for more ...   
1        I worked at IBM full-time for more than a year   
2                  I have been working at IBM full-time   
3       I worked at IBM full-time for more than 5 years   
4                  I have been working at IBM full-time   
...                                                 ...   
1445   I worked at IBM full-time for more than 10 years   
1446   I have been working at IBM  for more than a year   
1447  I have been working at IBM full-time for more ...   
1448  I have been working at IBM full-time for more ...   
1449  I have been working at IBM full-time for less ...   

                                                   Pros  \
0     Good clientele base and excellent project mana...   
1                     low workload\r\nwork life balance   
2               Flexible work timing, nice work culture   
3     Great managers\r\nGreat collagues\r\nGreat ben...   
4     innovation flexibility leadership good environ...   
...                                                 ...   
1445  Flexibility\r\nScope to move career within IBM...   
1446  Good work environment,satisfactory job, handfu...   
1447  great & Friendly atmosphere\r\nflexibility\r\n...   
1448  - Work/life Balance\r\n- Can work from  home d...   
1449  1.Lot of opportunities to grow.\r\n2.You desig...   

                                                   Cons Work/Life Balance  \
0     Company performance has hit the paid certifica...               4.0   
1     little career opportunities\r\nhard to get pro...               4.0   
2                                 Low year on year hike               5.0   
3     Isolated at times\r\nWFH a lot\r\nCommunicatio...               5.0   
4              promotion rating salary hike band change               NaN   
...                                                 ...               ...   
1445  not good pay unless you entered on high\r\nNo ...               4.0   
1446  Good hikes - don't expect, no free coffee or t...               4.0   
1447  few implementation projects\r\nlittle investme...               5.0   
1448  - IBM says they are a constantly adapting. Thi...               4.0   
1449  1.No proper Salary hike.\r\n2.Late recognizanc...               4.0   

     Culture & Values Career Opportunities Compensation & Benefits  \
0                 2.0                  2.0                     3.0   
1                 3.0                  3.0                     2.0   
2                 5.0                  4.0                     3.0   
3                 4.0                  4.0                     4.0   
4                 NaN                  NaN                     NaN   
...               ...                  ...                     ...   
1445              4.0                  4.0                     3.0   
1446              4.0                  4.0                     3.0   
1447              5.0                  4.0                     3.0   
1448              2.0                  3.0                     2.0   
1449              4.0                  3.0                     1.0   

     Senior Management  
0                  1.0  
1                  3.0  
2                  4.0  
3                  4.0  
4                  NaN  
...    

In [26]:
import pandas as pd
IBM = pd.concat([IBM,baidu3],ignore_index = True)
IBM

Title  \
0     "Good to join as fresher, IBM is best for lear...   
1                                      "Underestimated"   
2                           "Associate system engineer"   
3                                     "Data specialist"   
4                               "Application Developer"   
...                                                 ...   
9995  "Flexible, can support learning but not good pay"   
9996                  "Explore knowledge and learnings"   
9997                                "SAP SD Consultant"   
9998                     "Management is too old-school"   
9999               "Great company to start your Career"   

                                               WorkTime  \
0     I have been working at IBM full-time for more ...   
1     I have been working at IBM full-time for more ...   
2     I have been working at IBM full-time for more ...   
3                  I have been working at IBM full-time   
4                             I worked at IBM full-time   
...                                                 ...   
9995   I worked at IBM full-time for more than 10 years   
9996   I have been working at IBM  for more than a year   
9997  I have been working at IBM full-time for more ...   
9998  I have been working at IBM full-time for more ...   
9999  I have been working at IBM full-time for less ...   

                                                   Pros  \
0     --&gt; Good learning opportunity, mandatory to...   
1                    To gain some experience for future   
2                I m working in IBM from last two years   
3                       Good company to learn and grow.   
4                     Good company to start your career   
...                                                 ...   
9995  Flexibility\r\nScope to move career within IBM...   
9996  Good work environment,satisfactory job, handfu...   
9997  great & Friendly atmosphere\r\nflexibility\r\n...   
9998  - Work/life Balance\r\n- Can work from  home d...   
9999  1.Lot of opportunities to grow.\r\n2.You desig...   

                                                   Cons Work/Life Balance  \
0     Very low pay (independent of performance due t...               5.0   
1                         Good team and interesting job               4.0   
2     Worst Management . they will not give good rat...               4.0   
3                                Growth is slow in ibm.               4.0   
4                   Learning opportunities was less and               5.0   
...                                                 ...               ...   
9995  not good pay unless you entered on high\r\nNo ...               4.0   
9996  Good hikes - don't expect, no free coffee or t...               4.0   
9997  few implementation projects\r\nlittle investme...               5.0   
9998  - IBM says they are a constantly adapting. Thi...               4.0   
9999  1.No proper Salary hike.\r\n2.Late recognizanc...               4.0   

     Culture & Values Career Opportunities Compensation & Benefits  \
0                 5.0                  5.0                     3.0   
1                 3.0                  4.0                     1.0   
2                 4.0                  3.0                     3.0   
3                 4.0                  4.0                     3.0   
4                 5.0                  4.0                     4.0   
...               ...                  ...                     ...   
9995              4.0                  4.0                     3.0   
9996              4.0                  4.0                     3.0   
9997              5.0                  4.0                     3.0   
9998              2.0                  3.0                     2.0   
9999              4.0                  3.0                     1.0   

     Senior Management  
0                  5.0  
1                  1.0  
2                  4.0  
3                  4.0  
4                  5.0  
...    

In [44]:
IBM_3_2

Title  \
0                                                 "IBM"   
1                              "Global Project Manager"   
2                                             "My view"   
3                         "Not a so good place to work"   
4                                               "....."   
...                                                 ...   
4995  "Plenty of positions available, but limited op...   
4996                                                NaN   
4997                                                NaN   
4998                                                NaN   
4999                                                NaN   

                                               WorkTime  \
0                  I have been working at IBM full-time   
1     I have been working at IBM full-time for more ...   
2                           I have been working at IBM    
3     I have been working at IBM full-time for more ...   
4     I have been working at IBM full-time for more ...   
...                                                 ...   
4995  I have been working at IBM full-time for more ...   
4996                                                NaN   
4997                                                NaN   
4998                                                NaN   
4999                                                NaN   

                                                   Pros  \
0     Great people\r\nFlexibility\r\nWork-life balan...   
1     Great work-life balance, diversity of teams, g...   
2                         Awesome work and life balance   
3     Salary offered is fully fixed.... That is the ...   
4                    Work / life balance is pretty good   
...                                                 ...   
4995  higher management doesn't care employees' bene...   
4996                                                NaN   
4997                                                NaN   
4998                                                NaN   
4999                                                NaN   

                                                   Cons Work/Life Balance  \
0     Constant lay offs\r\nLow morale among employee...               4.0   
1     Compensation and benefits are very substandard...               5.0   
2     Can increase pay according to the market value...               5.0   
3     Growth opportunity is very minimal\nNot employ...               3.0   
4                     Salary compensation is pretty bad               4.0   
...                                                 ...               ...   
4995           Time flexibility, decent staff benefits.               4.0   
4996                                                NaN               2.0   
4997                                                NaN               5.0   
4998                                                NaN               1.0   
4999                                                NaN               5.0   

     Culture & Values Career Opportunities Compensation & Benefits  \
0                 2.0                  2.0                     3.0   
1                 5.0                  4.0                     3.0   
2                 3.0                  3.0                     2.0   
3                 3.0                  2.0                     4.0   
4                 3.0                  3.0                     1.0   
...               ...                  ...                     ...   
4995              1.0                  2.0                     1.0   
4996              1.0                  NaN                     1.0   
4997              5.0                  5.0                     2.0   
4998              3.0                  4.0                     2.0   
4999              4.0                  2.0                     4.0   

     Senior Management  
0                  2.0  
1                  3.0  
2                  NaN  
3                  3.0  
4                  3.0  
...    

In [27]:
IBM.to_csv('IBM_3001_3500.csv')

In [34]:
IBM_4 = pd.read_csv('IBM_4001_4500.csv')

In [35]:
IBM_4
#5710

Unnamed: 0                                              Title  \
0              0                                     "Good company"   
1              1  "Good experience but business direction is not...   
2              2                                      "IBM Ireland"   
3              3                              "Ibm  has many faces"   
4              4  "Good to start, then it depends what you want ...   
...          ...                                                ...   
5705        5705  "Treat emplyees a bit more than money making r...   
5706        5706  "It could be so much better with a bit of HR i...   
5707        5707  "US offices are probably a good place to be. F...   
5708        5708            "Could give Scrooge stinginess lessons"   
5709        5709                         "The Big Blue Sweat Shop."   

                                               WorkTime  \
0     I have been working at IBM full-time for more ...   
1     I have been working at IBM full-time for more ...   
2     I have been working at IBM full-time for more ...   
3     I have been working at IBM full-time for more ...   
4     I have been working at IBM full-time for more ...   
...                                                 ...   
5705                        I have been working at IBM    
5706                        I have been working at IBM    
5707                                   I worked at IBM    
5708                        I have been working at IBM    
5709                        I have been working at IBM    

                                                   Pros  \
0                         You can do something you like   
1     Flexible working environment and good atmosphere.   
2     Great place to hone your skills or up-skill.\r...   
3     You can work with nice, highly skilled and int...   
4     - Here in Dublin, IBM is growing, respect othe...   
...                                                 ...   
5705  Wide range of customers leading to some intere...   
5706  The company has a huge number of great people....   
5707                   Not too many good things to say.   
5708  The work can be interesting but they will make...   
5709  They are very innovative, and there are some v...   

                                                   Cons  Work/Life Balance  \
0               You may forced to change to other teams                5.0   
1     The business direction is not clear at the top...                4.0   
2     Payrises are few and far between, even if you ...                4.0   
3     Work very long hours, challenging to get incre...                2.0   
4     - As only few people got into the company afte...                4.0   
...                                                 ...                ...   
5705  Employees in Global business services ought to...                3.0   
5706  There is an old fashioned mentality one of mea...                4.5   
5707  Belgians! Working in EMEA, your life is contro...                2.5   
5708  Google might give free meals but IBM makes you...                4.0   
5709  IBM is a brutal company to work for.  It's so ...                3.0   

      Culture & Values  Career Opportunities  Compensation & Benefits  \
0                  3.0                   2.0                      3.0   
1                  3.0                   3.0                      3.0   
2                  3.0                   5.0                      2.0   
3                  4.0                   3.0                      2.0   
4                  2.0                   2.0                      2.0   
...                ...                   ...                      ...   
5705               NaN                   2.0                      2.5   
5706               NaN                   2.0                      1.5   
5707               NaN                   2.0                      3.5   
5708               NaN                   2.0                      1.

In [36]:
IBM_1 = pd.read_csv('IBM1000.csv')
IBM_1

Unnamed: 0                                         Title  \
0              0                               "great company"   
1              1                             "Good experience"   
2              2               "Great Place to Build a Career"   
3              3                         "Great place to work"   
4              4  "New CEO means new opportunities come April"   
...          ...                                           ...   
9985        9985                          "Awesome Experience"   
9986        9986                    "Manager played favorites"   
9987        9987                                  "Great Co.!"   
9988        9988                         "Junior Data Analyst"   
9989        9989                         "great place to work"   

                                               WorkTime  \
0       I worked at IBM full-time for more than 3 years   
1                  I have been working at IBM full-time   
2     I have been working at IBM full-time for more ...   
3                  I have been working at IBM full-time   
4     I have been working at IBM full-time for more ...   
...                                                 ...   
9985              I worked at IBM  for less than a year   
9986    I worked at IBM full-time for more than 3 years   
9987   I have been working at IBM  for more than a year   
9988              I worked at IBM  for more than a year   
9989                        I have been working at IBM    

                                                   Pros  \
0                      company treats it employees well   
1         Good experience\r\nLearned a lot\r\nGood team   
2     Top-notch company  focused on delivering the b...   
3     Plenty of experienced attorneys to learn from....   
4       respect for women, maternity/paternity time off   
...                                                 ...   
9985  The work culture and environment was very good...   
9986  If you like a company that tells you what to d...   
9987           Had a great relationship with colleagues   
9988  The best reason to work for IBM, one is its ba...   
9989  It is a great place to work. Cool projects, go...   

                                                   Cons  Work/Life Balance  \
0      lots of employees and employees  are not visable                4.0   
1                        No cons available at this time                NaN   
2     A big company with lots of initiative that can...                4.0   
3     Wish IBM allowed full time remote work from an...                4.0   
4      hierarchical, political, navigation can be tough                4.0   
...                                                 ...                ...   
9985                     Nothing I can think as of now.                5.0   
9986  Only worry about the bottom line in management...                3.0   
9987  Full-time position was not available at time o...                3.0   
9988             I did not have the opportunity to stay                2.0   
9989  Just like any other big companies, your happin...                5.0   

      Culture & Values  Career Opportunities  Compensation & Benefits  \
0                  4.0                   4.0                      4.0   
1                  NaN                   NaN                      NaN   
2                  5.0                   5.0                      5.0   
3                  4.0                   4.0                      4.0   
4                  4.0                   3.0                      3.0   
...                ...                   ...                      ...   
9985               4.0                   5.0                      4.0   
9986               2.0                   1.0                      3.0   
9987               5.0                   2.0                      3.0   
9988               2.0                   3.0                      2.0   
9989               NaN                   4.0           

In [47]:
IBM_1 = pd.read_csv('ibm1001-2000.csv')
IBM_1

Unnamed: 0                        Title  \
0              0               "Recruiter II"   
1              1                     "Intern"   
2              2   "Customer Support Manager"   
3              3  "Not the IBM it used to be"   
4              4                    "Analyst"   
...          ...                          ...   
9983        9983                "Good career"   
9984        9984                  "IBM India"   
9985        9985                          NaN   
9986        9986                          NaN   
9987        9987                          NaN   

                                               WorkTime  \
0     I have been working at IBM full-time for more ...   
1      I have been working at IBM  for less than a year   
2       I worked at IBM full-time for more than 8 years   
3      I worked at IBM full-time for more than 10 years   
4                                      I worked at IBM    
...                                                 ...   
9983  I have been working at IBM full-time for more ...   
9984  I have been working at IBM full-time for more ...   
9985                                                NaN   
9986                                                NaN   
9987                                                NaN   

                                                   Pros  \
0                    Constant Learning  and reinventing   
1     Good place to work, lots of learning opportuni...   
2     IBM was a great place to work.  They had excel...   
3     Flexible work options, including work from any...   
4     Without a doubt, the people I've worked with o...   
...                                                 ...   
9983  Innovation is key. You'll learn many technolog...   
9984  work life balance\r\ngreat learning opportunit...   
9985                                                NaN   
9986                                                NaN   
9987                                                NaN   

                                                   Cons  Work/Life Balance  \
0                      1 person in a very large company                5.0   
1              No negative experience for my internship                NaN   
2     Sometimes IBM can be slow to adjust to the mar...                5.0   
3     Toxic culture. Upper management only cares abo...                4.0   
4     None !!  If anyone could work with these peopl...                1.0   
...                                                 ...                ...   
9983  Moderate salary. Bureaucratic. Too many levels...                4.0   
9984   Can feel lost\r\nsalary hikes\r\nHR non existent                NaN   
9985                                                NaN                NaN   
9986                                                NaN                NaN   
9987                                                NaN                4.0   

      Culture & Values  Career Opportunities  Compensation & Benefits  \
0                  4.0                   5.0                      4.0   
1                  NaN                   NaN                      NaN   
2                  5.0                   5.0                      5.0   
3                  1.0                   2.0                      2.0   
4                  1.0                   1.0                      2.0   
...                ...                   ...                      ...   
9983               4.0                   4.0                      1.0   
9984               NaN                   NaN                      NaN   
9985               NaN                   NaN                      NaN   
9986               NaN                   NaN                      NaN   
9987               4.0                   4.0                      2.0   

      Senior Management  
0                   5.0  
1                   NaN  
2                   5.0  
3                   1.0  
4                   2.0  
...                 ...  
998

In [38]:
IBM = pd.concat([IBM_1, IBM],ignore_index = True)
IBM

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


Career Opportunities Compensation & Benefits  \
0                        4                       4   
1                      NaN                     NaN   
2                        5                       5   
3                        4                       4   
4                        3                       3   
...                    ...                     ...   
19985                  4.0                     3.0   
19986                  4.0                     3.0   
19987                  4.0                     3.0   
19988                  3.0                     2.0   
19989                  3.0                     1.0   

                                                    Cons Culture & Values  \
0       lots of employees and employees  are not visable                4   
1                         No cons available at this time              NaN   
2      A big company with lots of initiative that can...                5   
3      Wish IBM allowed full time remote work from an...                4   
4       hierarchical, political, navigation can be tough                4   
...                                                  ...              ...   
19985  not good pay unless you entered on high\r\nNo ...              4.0   
19986  Good hikes - don't expect, no free coffee or t...              4.0   
19987  few implementation projects\r\nlittle investme...              5.0   
19988  - IBM says they are a constantly adapting. Thi...              2.0   
19989  1.No proper Salary hike.\r\n2.Late recognizanc...              4.0   

                                                    Pros Senior Management  \
0                       company treats it employees well                 4   
1          Good experience\r\nLearned a lot\r\nGood team               NaN   
2      Top-notch company  focused on delivering the b...                 4   
3      Plenty of experienced attorneys to learn from....                 3   
4        respect for women, maternity/paternity time off                 3   
...                                                  ...               ...   
19985  Flexibility\r\nScope to move career within IBM...               3.0   
19986  Good work environment,satisfactory job, handfu...               4.0   
19987  great & Friendly atmosphere\r\nflexibility\r\n...               4.0   
19988  - Work/life Balance\r\n- Can work from  home d...               1.0   
19989  1.Lot of opportunities to grow.\r\n2.You desig...               2.0   

                                                   Title  Unnamed: 0  \
0                                        "great company"         0.0   
1                                      "Good experience"         1.0   
2                        "Great Place to Build a Career"         2.0   
3                                  "Great place to work"         3.0   
4           "New CEO means new opportunities come April"         4.0   
...                                                  ...         ...   
19985  "Flexible, can support learning but not good pay"         NaN   
19986                  "Explore knowledge and learnings"         NaN   
19987                                "SAP SD Consultant"         NaN   
19988                     "Management is too old-school"         NaN   
19989               "Great company to start your Career"         NaN   

      Work/Life Balance                                           WorkTime  
0                     4    I worked at IBM full-time for more than 3 years  
1                   NaN               I have been working at IBM full-time  
2                     4  I have been working at IBM full-time for more ...  
3                     4               I have been working at IBM full-time  
4                     4  I have been working at IBM full-time for more ...  
...                 ...                                                ...  
19985               4.0   I worked at IBM full-time for more than 10 years  
19986         

In [45]:
IBM = pd.concat([IBM, IBM_3_2],ignore_index = True)
IBM

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


Career Opportunities Compensation & Benefits  \
0                        4                       4   
1                      NaN                     NaN   
2                        5                       5   
3                        4                       4   
4                        3                       3   
...                    ...                     ...   
35695                  2.0                     1.0   
35696                  NaN                     1.0   
35697                  5.0                     2.0   
35698                  4.0                     2.0   
35699                  2.0                     4.0   

                                                    Cons Culture & Values  \
0       lots of employees and employees  are not visable                4   
1                         No cons available at this time              NaN   
2      A big company with lots of initiative that can...                5   
3      Wish IBM allowed full time remote work from an...                4   
4       hierarchical, political, navigation can be tough                4   
...                                                  ...              ...   
35695           Time flexibility, decent staff benefits.              1.0   
35696                                                NaN              1.0   
35697                                                NaN              5.0   
35698                                                NaN              3.0   
35699                                                NaN              4.0   

                                                    Pros Senior Management  \
0                       company treats it employees well                 4   
1          Good experience\r\nLearned a lot\r\nGood team               NaN   
2      Top-notch company  focused on delivering the b...                 4   
3      Plenty of experienced attorneys to learn from....                 3   
4        respect for women, maternity/paternity time off                 3   
...                                                  ...               ...   
35695  higher management doesn't care employees' bene...               3.0   
35696                                                NaN               1.0   
35697                                                NaN               4.0   
35698                                                NaN               3.0   
35699                                                NaN               3.0   

                                                   Title  Unnamed: 0  \
0                                        "great company"         0.0   
1                                      "Good experience"         1.0   
2                        "Great Place to Build a Career"         2.0   
3                                  "Great place to work"         3.0   
4           "New CEO means new opportunities come April"         4.0   
...                                                  ...         ...   
35695  "Plenty of positions available, but limited op...         NaN   
35696                                                NaN         NaN   
35697                                                NaN         NaN   
35698                                                NaN         NaN   
35699                                                NaN         NaN   

      Work/Life Balance                                           WorkTime  
0                     4    I worked at IBM full-time for more than 3 years  
1                   NaN               I have been working at IBM full-time  
2                     4  I have been working at IBM full-time for more ...  
3                     4               I have been working at IBM full-time  
4                     4  I have been working at IBM full-time for more ...  
...                 ...                                                ...  
35695               4.0  I have been working at IBM full-time for more ...  
35696         

In [46]:
IBM.to_csv('IBM.csv')

In [10]:
import pandas as pd
IBM = pd.read_csv('IBM.csv')

In [11]:
IBM


Unnamed: 0  Career Opportunities  Compensation & Benefits  \
0               0                   4.0                      4.0   
1               1                   NaN                      NaN   
2               2                   5.0                      5.0   
3               3                   4.0                      4.0   
4               4                   3.0                      3.0   
...           ...                   ...                      ...   
35695       35695                   2.0                      1.0   
35696       35696                   NaN                      1.0   
35697       35697                   5.0                      2.0   
35698       35698                   4.0                      2.0   
35699       35699                   2.0                      4.0   

                                                    Cons  Culture & Values  \
0       lots of employees and employees  are not visable               4.0   
1                         No cons available at this time               NaN   
2      A big company with lots of initiative that can...               5.0   
3      Wish IBM allowed full time remote work from an...               4.0   
4       hierarchical, political, navigation can be tough               4.0   
...                                                  ...               ...   
35695           Time flexibility, decent staff benefits.               1.0   
35696                                                NaN               1.0   
35697                                                NaN               5.0   
35698                                                NaN               3.0   
35699                                                NaN               4.0   

                                                    Pros  Senior Management  \
0                       company treats it employees well                4.0   
1          Good experience\r\nLearned a lot\r\nGood team                NaN   
2      Top-notch company  focused on delivering the b...                4.0   
3      Plenty of experienced attorneys to learn from....                3.0   
4        respect for women, maternity/paternity time off                3.0   
...                                                  ...                ...   
35695  higher management doesn't care employees' bene...                3.0   
35696                                                NaN                1.0   
35697                                                NaN                4.0   
35698                                                NaN                3.0   
35699                                                NaN                3.0   

                                                   Title  Unnamed: 0.1  \
0                                        "great company"           0.0   
1                                      "Good experience"           1.0   
2                        "Great Place to Build a Career"           2.0   
3                                  "Great place to work"           3.0   
4           "New CEO means new opportunities come April"           4.0   
...                                                  ...           ...   
35695  "Plenty of positions available, but limited op...           NaN   
35696                                                NaN           NaN   
35697                                                NaN           NaN   
35698                                                NaN           NaN   
35699                                                NaN           NaN   

       Work/Life Balance                                           WorkTime  
0                    4.0    I worked at IBM full-time for more than 3 years  
1                    NaN               I have been working at IBM full-time  
2                    4.0  I have been working at IBM full-time for more ...  
3                    4.0               I have been working at IBM full-time  
4                    4.0 

In [13]:
IBM= IBM[:-500]

In [14]:
IBM

Unnamed: 0  Career Opportunities  Compensation & Benefits  \
0               0                   4.0                      4.0   
1               1                   NaN                      NaN   
2               2                   5.0                      5.0   
3               3                   4.0                      4.0   
4               4                   3.0                      3.0   
...           ...                   ...                      ...   
35195       35195                   4.0                      3.0   
35196       35196                   2.0                      2.0   
35197       35197                   3.0                      3.0   
35198       35198                   4.0                      4.0   
35199       35199                   2.0                      2.0   

                                                    Cons  Culture & Values  \
0       lots of employees and employees  are not visable               4.0   
1                         No cons available at this time               NaN   
2      A big company with lots of initiative that can...               5.0   
3      Wish IBM allowed full time remote work from an...               4.0   
4       hierarchical, political, navigation can be tough               4.0   
...                                                  ...               ...   
35195  This is a bit contradictive assessment as the ...               4.0   
35196  work from home opt not available to most of th...               3.0   
35197  It has become too big and obsessed with the bo...               3.0   
35198  HR evolution\r\nPossibility to have new jobs a...               3.0   
35199  Heavy workload and sometimes boring and repeti...               4.0   

                                                    Pros  Senior Management  \
0                       company treats it employees well                4.0   
1          Good experience\r\nLearned a lot\r\nGood team                NaN   
2      Top-notch company  focused on delivering the b...                4.0   
3      Plenty of experienced attorneys to learn from....                3.0   
4        respect for women, maternity/paternity time off                3.0   
...                                                  ...                ...   
35195  It's a brilliant opportunity to learn how mult...                4.0   
35196   work from home option available to some employee                2.0   
35197  IBM has a very large expertise pool. It provid...                3.0   
35198                          Manage work and life time                2.0   
35199             Friendly colleagues and nice workplace                3.0   

                                                   Title  Unnamed: 0.1  \
0                                        "great company"           0.0   
1                                      "Good experience"           1.0   
2                        "Great Place to Build a Career"           2.0   
3                                  "Great place to work"           3.0   
4           "New CEO means new opportunities come April"           4.0   
...                                                  ...           ...   
35195  "Great place to learn - lot of waste because o...           NaN   
35196                                "Work life balance"           NaN   
35197  "A mixed bag with some great people with terri...           NaN   
35198             "Solid corporate but low HR evolution"           NaN   
35199                                             "Good"           NaN   

       Work/Life Balance                                           WorkTime  
0                    4.0    I worked at IBM full-time for more than 3 years  
1                    NaN               I have been working at IBM full-time  
2                    4.0  I have been working at IBM full-time for more ...  
3                    4.0               I have been working at IBM full-time  
4                    4.0 

In [17]:
IBM_sum = pd.concat([IBM, IBM_1],ignore_index = True)
IBM_sum

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


Career Opportunities  Compensation & Benefits  \
0                       4.0                      4.0   
1                       NaN                      NaN   
2                       5.0                      5.0   
3                       4.0                      4.0   
4                       3.0                      3.0   
...                     ...                      ...   
43680                   4.0                      1.0   
43681                   NaN                      NaN   
43682                   NaN                      NaN   
43683                   NaN                      NaN   
43684                   4.0                      2.0   

                                                    Cons  Culture & Values  \
0       lots of employees and employees  are not visable               4.0   
1                         No cons available at this time               NaN   
2      A big company with lots of initiative that can...               5.0   
3      Wish IBM allowed full time remote work from an...               4.0   
4       hierarchical, political, navigation can be tough               4.0   
...                                                  ...               ...   
43680              Salary increase is like day dreaming.               4.0   
43681           Nothing in general\r\nEverything is good               NaN   
43682           Less team work and management in growth.               NaN   
43683  Moderate salary. Bureaucratic. Too many levels...               NaN   
43684   Can feel lost\r\nsalary hikes\r\nHR non existent               4.0   

                                                    Pros  Senior Management  \
0                       company treats it employees well                4.0   
1          Good experience\r\nLearned a lot\r\nGood team                NaN   
2      Top-notch company  focused on delivering the b...                4.0   
3      Plenty of experienced attorneys to learn from....                3.0   
4        respect for women, maternity/paternity time off                3.0   
...                                                  ...                ...   
43680  Work Life balance,  Good Clients, Exposure to ...                3.0   
43681                       Good place for women to work                NaN   
43682   Good work time management and work life balance.                NaN   
43683  Innovation is key. You'll learn many technolog...                NaN   
43684  work life balance\r\ngreat learning opportunit...                4.0   

                                              Title  Unnamed: 0  Unnamed: 0.1  \
0                                   "great company"           0           0.0   
1                                 "Good experience"           1           1.0   
2                   "Great Place to Build a Career"           2           2.0   
3                             "Great place to work"           3           3.0   
4      "New CEO means new opportunities come April"           4           4.0   
...                                             ...         ...           ...   
43680                          "Technical services"        8480           NaN   
43681                    "Review about the company"        8481           NaN   
43682                               "Data Engineer"        8482           NaN   
43683                                 "Good career"        8483           NaN   
43684                                   "IBM India"        8484           NaN   

       Work/Life Balance                                           WorkTime  
0                    4.0    I worked at IBM full-time for more than 3 years  
1                    NaN               I have been working at IBM full-time  
2                    4.0  I have been working at IBM full-time for more ...  
3                    4.0               I have been working at IBM full-time  
4                    4.0  I have been working at IBM full-time for more ...  
...    

In [15]:
IBM_1 = pd.read_csv('IBM1000_2000.csv')

In [18]:
IBM_sum.to_csv('IBM_sum.csv')